In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sb
%matplotlib inline    
from sklearn.model_selection import train_test_split
from numpy import mean
from numpy import std

from sklearn.svm import SVC
from sklearn.metrics import accuracy_score

from sklearn.linear_model import LinearRegression
from sklearn.metrics import mean_squared_error

In [2]:
x_train_all = pd.read_csv('../Datasets/X_Train Without Yeo Johnson 70-30.csv')

x_test_all = pd.read_csv('../Datasets/X_Test Without Yeo Johnson 70-30.csv')

y_train_all = pd.read_csv('../Datasets/Y_Train Without Yeo Johnson 70-30.csv')

y_test_all = pd.read_csv('../Datasets/Y_Test Without Yeo Johnson  70-30.csv')

In [3]:
parameters = [
    ['HbA1c', 'BMI', 'AGE', 'Chol'],
    ['HbA1c', 'BMI', 'AGE', 'Chol', 'TG'],
    ['HbA1c', 'BMI', 'AGE', 'Chol', 'TG', 'VLDL', 'LDL'],
    ['HbA1c', 'BMI', 'AGE', 'Chol', 'TG', 'VLDL', 'LDL', 'Cr', 'HDL']
]

In [4]:
hyper_params = {}
i = 0
j = 0
svc_param = []
lr_param = []
knn_param = []
column = ["Feature 4", "Feature 5", "Feature 7", "Feature 9"]
hyper_params['Column'] = column

In [5]:
metrics = ["Accuracy", "Precision", "Recall", "F1 Score", "Cohen Kappa", "AUC"]

performance_dict = {}
performance_dict['Metrics'] = metrics

metrics_grid = ["Accuracy", "Precision", "Recall", "F1 Score", "Cohen Kappa", "AUC"]

performance_dict_grid = {}
performance_dict_grid['Metrics'] = metrics_grid

In [6]:
for param in parameters:
    x_train = x_train_all[param]
    y_train = y_train_all
    x_test = x_test_all[param]
    y_test = y_test_all
    # Support Vector Classifier Train, Test 

    from sklearn.svm import SVC
    from sklearn.metrics import accuracy_score
    modelSVC = SVC(probability=True)
    modelSVC.fit(x_train, y_train)
    #modelSVC.fit(x_test, y_test)
    #print(modelSVC.score(x_test, y_test))

    y_pred_svc = modelSVC.predict(x_test)
    #y_pred = modelSVC.predict(x_train)
    svc_acc = accuracy_score(y_test, y_pred_svc)
    #ac = accuracy_score(y_train, y_pred)
    print(svc_acc)

    from sklearn.metrics import confusion_matrix
    from sklearn.metrics import classification_report

    print(confusion_matrix(y_test, y_pred_svc))
    print(classification_report(y_test, y_pred_svc))

    from sklearn.metrics import cohen_kappa_score, f1_score, precision_score, recall_score, roc_auc_score

    cmSVC = confusion_matrix(y_test, modelSVC.predict(x_test))

    #If we use TP TN FP and FN of below's comment we get range
    #FP = cmSVC.sum(axis=0) - np.diag(cmSVC)  
    #FN = cmSVC.sum(axis=1) - np.diag(cmSVC)
    #TP = np.diag(cmSVC)
    #TN = cmSVC.sum() - (FP + FN + TP)

    TP = cmSVC[1,1]  
    TN = cmSVC[0,0] 
    FP = cmSVC[0,1] 
    FN = cmSVC[1,0] 

    # Sensitivity, hit rate, recall, or true positive rate
    TPR = TP/float(TP+FN)
    # Specificity or true negative rate
    TNR = TN/float(TN+FP) 
    # Precision or positive predictive value
    PPV = TP/float(TP+FP)
    # Negative predictive value
    NPV = TN/float(TN+FN)
    # Fall out or false positive rate
    FPR = FP/float(FP+TN)
    # False negative rate
    FNR = FN/float(TP+FN)
    # False discovery rate
    FDR = FP/float(TP+FP)
    totalSVC=sum(sum(cmSVC))
    Accuracy = (TN+TP)/totalSVC
    # MCC
    val = (TP * TN) - (FP * FN)
    MCC_SVC = val / np.sqrt((TP + FP) * (TP + FN) * (TN + FP) * (TN + FN))



    Y_pred_svc = modelSVC.predict(x_test)


    cohen_score = cohen_kappa_score(y_test, Y_pred_svc)
    f1 = f1_score(y_test, Y_pred_svc, average = "weighted")
    precision = precision_score(y_test, Y_pred_svc, average = "weighted")
    recall = recall_score(y_test, Y_pred_svc, average = "weighted")

    pred_prob = modelSVC.predict_proba(x_test)
    auc_score = roc_auc_score(y_test, pred_prob, multi_class='ovr')

    print(f"Precision  {precision}")
    print(f"f1 Score  {f1}")
    print(f"Recall  {recall}")
    specificity = TNR
    print("Specificity/TNR: " + str(TNR))
    print("Cohen Kappa: " + str(cohen_score))
    print(f"AUC Score  {auc_score}")

    svc_performances = [svc_acc, precision, recall, f1, cohen_score, auc_score ]
    performance_dict['SVC'] = svc_performances

    performance_dict

    # Supper Vector Classifier Hyperparameter Tuning GridSearchCV

    from sklearn.model_selection import GridSearchCV
    GSCV_SVC = GridSearchCV(modelSVC,{
        'C': [1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20],
        'gamma': [1, 0.1, 0.01, 0.001, 0.0001],
        'kernel':['rbf', 'linear', 'poly', 'sigmoid']
    }, 
    cv = 10, 
    return_train_score = False
    )
    GSCV_SVC.fit(x_train, y_train)
    GSCV_SVC.cv_results_

    df_svc_grid = pd.DataFrame(GSCV_SVC.cv_results_)
    df_svc_grid

    df_svc_grid[['param_C', 'param_kernel', 'mean_test_score']]

    # print(GSCV_SVC.best_score_)
    gscv_svc_acc = GSCV_SVC.best_score_
    # print(GSCV_SVC.best_params_)
    
    svc_param.append(GSCV_SVC.best_params_)
    
    grid_predictions = GSCV_SVC.predict(x_test)

    # print classification report
    print(classification_report(y_test, grid_predictions))

    from sklearn.metrics import cohen_kappa_score, f1_score, precision_score, recall_score, roc_auc_score

    cmSVC = confusion_matrix(y_test, GSCV_SVC.predict(x_test))

    #If we use TP TN FP and FN of below's comment we get range
    #FP = cmSVC.sum(axis=0) - np.diag(cmSVC)  
    #FN = cmSVC.sum(axis=1) - np.diag(cmSVC)
    #TP = np.diag(cmSVC)
    #TN = cmSVC.sum() - (FP + FN + TP)

    TP = cmSVC[1,1]  
    TN = cmSVC[0,0] 
    FP = cmSVC[0,1] 
    FN = cmSVC[1,0] 

    # Sensitivity, hit rate, recall, or true positive rate
    TPR = TP/float(TP+FN)
    # Specificity or true negative rate
    TNR = TN/float(TN+FP) 
    # Precision or positive predictive value
    PPV = TP/float(TP+FP)
    # Negative predictive value
    NPV = TN/float(TN+FN)
    # Fall out or false positive rate
    FPR = FP/float(FP+TN)
    # False negative rate
    FNR = FN/float(TP+FN)
    # False discovery rate
    FDR = FP/float(TP+FP)
    totalSVC=sum(sum(cmSVC))
    Accuracy = (TN+TP)/totalSVC
    # MCC
    val = (TP * TN) - (FP * FN)
    MCC_SVC = val / np.sqrt((TP + FP) * (TP + FN) * (TN + FP) * (TN + FN))



    y_pred_svc_grid = GSCV_SVC.predict(x_test)


    cohen_score = cohen_kappa_score(y_test, y_pred_svc_grid)
    f1 = f1_score(y_test, y_pred_svc_grid, average = "weighted")
    precision = precision_score(y_test, y_pred_svc_grid, average = "weighted")
    recall = recall_score(y_test, y_pred_svc_grid, average = "weighted")

    pred_prob = GSCV_SVC.predict_proba(x_test)
    auc_score = roc_auc_score(y_test, pred_prob, multi_class='ovr')

    print(f"Precision  {precision}")
    print(f"f1 Score  {f1}")
    print(f"Recall  {recall}")
    specificity = TNR
    print("Specificity/TNR: " + str(TNR))
    print("Cohen Kappa: " + str(cohen_score))
    print(f"AUC Score  {auc_score}")

    svc_performances_grid = [gscv_svc_acc, precision, recall, f1, cohen_score, auc_score ]
    performance_dict_grid['SVC'] = svc_performances_grid

    performance_dict_grid

    # Logistic Regression Train, Test

    from sklearn.linear_model import LogisticRegression
    from sklearn.metrics import accuracy_score

    modelLR = LogisticRegression()
    modelLR.fit(x_train, y_train)

    y_pred_lr = modelLR.predict(x_test)
    lr_ac = accuracy_score(y_test, y_pred_lr)

    print("Training Accuracy: {:.3f}".format(modelLR.score(x_train, y_train)))
    print("Testing Accuracy: {:.3f}".format(modelLR.score(x_test, y_test)))

    print(confusion_matrix(y_test, y_pred_lr))
    print(classification_report(y_test, y_pred_lr))

    from sklearn.metrics import cohen_kappa_score
    cmRFC = confusion_matrix(y_test, modelLR.predict(x_test))

    #If we use TP TN FP and FN of below's comment we get range
    #FP = cmSVC.sum(axis=0) - np.diag(cmSVC)  
    #FN = cmSVC.sum(axis=1) - np.diag(cmSVC)
    #TP = np.diag(cmSVC)
    #TN = cmSVC.sum() - (FP + FN + TP)

    TP = cmRFC[1,1]  
    TN = cmRFC[0,0] 
    FP = cmRFC[0,1] 
    FN = cmRFC[1,0] 

    # Sensitivity, hit rate, recall, or true positive rate
    TPR = TP/float(TP+FN)
    # Specificity or true negative rate
    TNR = TN/float(TN+FP) 
    # Precision or positive predictive value
    PPV = TP/float(TP+FP)
    # Negative predictive value
    NPV = TN/float(TN+FN)
    # Fall out or false positive rate
    FPR = FP/float(FP+TN)
    # False negative rate
    FNR = FN/float(TP+FN)
    # False discovery rate
    FDR = FP/float(TP+FP)
    # Accuracy
    totalRFC=sum(sum(cmRFC))
    Accuracy = (TN+TP)/totalRFC
    # MCC
    val = (TP * TN) - (FP * FN)
    MCC_RFC = val / np.sqrt((TP + FP) * (TP + FN) * (TN + FP) * (TN + FN))
    # Cohen Kappa
    Y_pred_lr = modelLR.predict(x_test)
    pred_prob = modelLR.predict_proba(x_test)


    cohen_score = cohen_kappa_score(y_test, Y_pred_lr)
    f1 = f1_score(y_test, Y_pred_lr, average = "weighted")
    precision = precision_score(y_test, Y_pred_lr, average = "weighted")
    recall = recall_score(y_test, Y_pred_lr, average = "weighted")


    auc_score = roc_auc_score(y_test, pred_prob, multi_class='ovr')

    print(f"Precision  {precision}")
    print(f"f1 Score  {f1}")
    print(f"Recall  {recall}")
    specificity = TNR
    print("Specificity/TNR: " + str(TNR))

    print("Cohen Kappa: " + str(cohen_score))
    print(f"AUC Score  {auc_score}")

    rfc_performances = [lr_ac, precision, recall, f1, cohen_score, auc_score ]
    performance_dict['LR'] = rfc_performances

    performance_dict

    # Logistic Regression Hyperparameter Tuning GridSearchCV

    from sklearn import linear_model

    C = np.logspace(0, 4, 10)
    penalty = ['l1', 'l2']
    solver = ['liblinear', 'saga']
    hyperparameters = dict(C=C, penalty=penalty, solver=solver)
    logistic = linear_model.LogisticRegression()
    GSCV_LR = GridSearchCV(logistic, hyperparameters, cv = 10)
    GSCV_LR.fit(x_train, y_train)
    GSCV_LR.cv_results_

    df_lr_grid = pd.DataFrame(GSCV_LR.cv_results_)
    df_lr_grid

    df_lr_grid[['param_C', 'mean_test_score']]

    # print(GSCV_LR.best_score_)
    gscv_lr_acc = GSCV_LR.best_score_
    # print(GSCV_LR.best_params_)
    
    lr_param.append(GSCV_LR.best_params_)
    grid_predictions = GSCV_LR.predict(x_test)

    # print classification report
    print(classification_report(y_test, grid_predictions))

    from sklearn.metrics import cohen_kappa_score
    cmRFC = confusion_matrix(y_test, GSCV_LR.predict(x_test))

    #If we use TP TN FP and FN of below's comment we get range
    #FP = cmSVC.sum(axis=0) - np.diag(cmSVC)  
    #FN = cmSVC.sum(axis=1) - np.diag(cmSVC)
    #TP = np.diag(cmSVC)
    #TN = cmSVC.sum() - (FP + FN + TP)

    TP = cmRFC[1,1]  
    TN = cmRFC[0,0] 
    FP = cmRFC[0,1] 
    FN = cmRFC[1,0] 

    # Sensitivity, hit rate, recall, or true positive rate
    TPR = TP/float(TP+FN)
    # Specificity or true negative rate
    TNR = TN/float(TN+FP) 
    # Precision or positive predictive value
    PPV = TP/float(TP+FP)
    # Negative predictive value
    NPV = TN/float(TN+FN)
    # Fall out or false positive rate
    FPR = FP/float(FP+TN)
    # False negative rate
    FNR = FN/float(TP+FN)
    # False discovery rate
    FDR = FP/float(TP+FP)
    # Accuracy
    totalRFC=sum(sum(cmRFC))
    Accuracy = (TN+TP)/totalRFC
    # MCC
    val = (TP * TN) - (FP * FN)
    MCC_RFC = val / np.sqrt((TP + FP) * (TP + FN) * (TN + FP) * (TN + FN))
    # Cohen Kappa
    Y_pred_lr_grid = GSCV_LR.predict(x_test)
    pred_prob = GSCV_LR.predict_proba(x_test)


    cohen_score = cohen_kappa_score(y_test, Y_pred_lr_grid)
    f1 = f1_score(y_test, Y_pred_lr_grid, average = "weighted")
    precision = precision_score(y_test, Y_pred_lr_grid, average = "weighted")
    recall = recall_score(y_test, Y_pred_lr_grid, average = "weighted")


    auc_score = roc_auc_score(y_test, pred_prob, multi_class='ovr')

    print(f"Precision  {precision}")
    print(f"f1 Score  {f1}")
    print(f"Recall  {recall}")
    specificity = TNR
    print("Specificity/TNR: " + str(TNR))

    print("Cohen Kappa: " + str(cohen_score))
    print(f"AUC Score  {auc_score}")

    lr_performances_grid = [gscv_lr_acc, precision, recall, f1, cohen_score, auc_score ]
    performance_dict_grid['LR'] = lr_performances_grid

    performance_dict_grid

    # KNN Train, Test

    from sklearn.neighbors import KNeighborsClassifier
    from sklearn.metrics import accuracy_score


    modelKNN = KNeighborsClassifier() #, algorithm = 'ball_tree', weights = 'distance', metric = 'minkowski', p = 2
    modelKNN.fit(x_train, y_train)
    print(modelKNN.score(x_test, y_test))

    # Predicting the Test set results
    y_pred_knn = modelKNN.predict(x_test)
    ac = accuracy_score(y_test, y_pred_knn)
    print(accuracy_score(y_test, y_pred_knn))
    print(confusion_matrix(y_test, y_pred_knn))
    print(classification_report(y_test, y_pred_knn))

    from sklearn.metrics import cohen_kappa_score
    cmKNN = confusion_matrix(y_test, modelKNN.predict(x_test))

    #If we use TP TN FP and FN of below's comment we get range
    #FP = cmSVC.sum(axis=0) - np.diag(cmSVC)  
    #FN = cmSVC.sum(axis=1) - np.diag(cmSVC)
    #TP = np.diag(cmSVC)
    #TN = cmSVC.sum() - (FP + FN + TP)

    TP = cmKNN[1,1]  
    TN = cmKNN[0,0] 
    FP = cmKNN[0,1] 
    FN = cmKNN[1,0] 

    # Sensitivity, hit rate, recall, or true positive rate
    TPR = TP/float(TP+FN)
    # Specificity or true negative rate
    TNR = TN/float(TN+FP) 
    # Precision or positive predictive value
    PPV = TP/float(TP+FP)
    # Negative predictive value
    NPV = TN/float(TN+FN)
    # Fall out or false positive rate
    FPR = FP/float(FP+TN)
    # False negative rate
    FNR = FN/float(TP+FN)
    # False discovery rate
    FDR = FP/float(TP+FP)
    # Accuracy
    totalKNN = sum(sum(cmKNN))
    Accuracy = (TN+TP)/totalKNN
    # MCC
    val = (TP * TN) - (FP * FN)
    MCC_KNN = val / np.sqrt((TP + FP) * (TP + FN) * (TN + FP) * (TN + FN))
    # Cohen Kappa
    Y_pred_knn = modelKNN.predict(x_test)
    pred_prob = modelKNN.predict_proba(x_test)


    cohen_score = cohen_kappa_score(y_test, Y_pred_knn)
    f1 = f1_score(y_test, Y_pred_knn, average = "weighted")
    precision = precision_score(y_test, Y_pred_knn, average = "weighted")
    recall = recall_score(y_test, Y_pred_knn, average = "weighted")


    auc_score = roc_auc_score(y_test, pred_prob, multi_class='ovr')

    print(f"Precision  {precision}")
    print(f"f1 Score  {f1}")
    print(f"Recall  {recall}")
    specificity = TNR
    print("Specificity/TNR: " + str(TNR))

    print("Cohen Kappa: " + str(cohen_score))
    print(f"AUC Score  {auc_score}")


    # metrics = ["Accuracy", "Precision", "Recall", "F1 Score", "Specificity", "Cohen Kappa", "AUC"]
    knn_performances = [ac, precision, recall, f1, cohen_score, auc_score ]
    performance_dict['KNN'] = knn_performances

    performance_dict

    # Logistic Regression Hyperparameter Tuning GridSearchCV

    grid_params = { 'n_neighbors' : [1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20],
                   'weights' : ['uniform','distance'],
                   'metric' : ['minkowski','euclidean','manhattan']}

    GSCV_KNN = GridSearchCV(KNeighborsClassifier(), grid_params, verbose = 1, cv = 10, n_jobs = -1)
    GSCV_KNN.fit(x_train, y_train)
    GSCV_KNN.cv_results_

    df_knn_grid = pd.DataFrame(GSCV_KNN.cv_results_)
    df_knn_grid

    df_knn_grid[['param_metric', 'param_n_neighbors', 'mean_test_score']]

    # print(GSCV_KNN.best_score_)
    gscv_knn_acc = GSCV_KNN.best_score_
    # print(GSCV_KNN.best_params_)
    
    knn_param.append(GSCV_KNN.best_params_)
    
    grid_predictions = GSCV_KNN.predict(x_test)

    # print classification report
    print(classification_report(y_test, grid_predictions))

    from sklearn.metrics import cohen_kappa_score
    cmRFC = confusion_matrix(y_test, GSCV_KNN.predict(x_test))

    #If we use TP TN FP and FN of below's comment we get range
    #FP = cmSVC.sum(axis=0) - np.diag(cmSVC)  
    #FN = cmSVC.sum(axis=1) - np.diag(cmSVC)
    #TP = np.diag(cmSVC)
    #TN = cmSVC.sum() - (FP + FN + TP)

    TP = cmRFC[1,1]  
    TN = cmRFC[0,0] 
    FP = cmRFC[0,1] 
    FN = cmRFC[1,0] 

    # Sensitivity, hit rate, recall, or true positive rate
    TPR = TP/float(TP+FN)
    # Specificity or true negative rate
    TNR = TN/float(TN+FP) 
    # Precision or positive predictive value
    PPV = TP/float(TP+FP)
    # Negative predictive value
    NPV = TN/float(TN+FN)
    # Fall out or false positive rate
    FPR = FP/float(FP+TN)
    # False negative rate
    FNR = FN/float(TP+FN)
    # False discovery rate
    FDR = FP/float(TP+FP)
    # Accuracy
    totalRFC=sum(sum(cmRFC))
    Accuracy = (TN+TP)/totalRFC
    # MCC
    val = (TP * TN) - (FP * FN)
    MCC_RFC = val / np.sqrt((TP + FP) * (TP + FN) * (TN + FP) * (TN + FN))
    # Cohen Kappa
    Y_pred_knn_grid = GSCV_KNN.predict(x_test)
    pred_prob = GSCV_KNN.predict_proba(x_test)


    cohen_score = cohen_kappa_score(y_test, Y_pred_knn_grid)
    f1 = f1_score(y_test, Y_pred_knn_grid, average = "weighted")
    precision = precision_score(y_test, Y_pred_knn_grid, average = "weighted")
    recall = recall_score(y_test, Y_pred_knn_grid, average = "weighted")


    auc_score = roc_auc_score(y_test, pred_prob, multi_class='ovr')

    print(f"Precision  {precision}")
    print(f"f1 Score  {f1}")
    print(f"Recall  {recall}")
    specificity = TNR
    print("Specificity/TNR: " + str(TNR))

    print("Cohen Kappa: " + str(cohen_score))
    print(f"AUC Score  {auc_score}")

    knn_performances_grid = [gscv_knn_acc, precision, recall, f1, cohen_score, auc_score ]
    performance_dict_grid['KNN'] = knn_performances_grid

    performance_dict_grid

C:\Users\babar\anaconda3\lib\site-packages\sklearn\utils\validation.py:993: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\babar\anaconda3\lib\site-packages\sklearn\utils\validation.py:993: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\babar\anaconda3\lib\site-packages\sklearn\utils\validation.py:993: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\babar\anaconda3\lib\site-packages\sklearn\utils\validation.py:993: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), 

0.9637096774193549
[[ 22   0   1]
 [  2   3   2]
 [  4   0 214]]
              precision    recall  f1-score   support

           0       0.79      0.96      0.86        23
           1       1.00      0.43      0.60         7
           2       0.99      0.98      0.98       218

    accuracy                           0.96       248
   macro avg       0.92      0.79      0.82       248
weighted avg       0.97      0.96      0.96       248

Precision  0.9679742084138546
f1 Score  0.9618350454753647
Recall  0.9637096774193549
Specificity/TNR: 1.0
Cohen Kappa: 0.8350698293061405
AUC Score  0.9901118514737147


C:\Users\babar\anaconda3\lib\site-packages\sklearn\utils\validation.py:993: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\babar\anaconda3\lib\site-packages\sklearn\utils\validation.py:993: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\babar\anaconda3\lib\site-packages\sklearn\utils\validation.py:993: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\babar\anaconda3\lib\site-packages\sklearn\utils\validation.py:993: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), 

              precision    recall  f1-score   support

           0       0.77      1.00      0.87        23
           1       1.00      0.57      0.73         7
           2       1.00      0.98      0.99       218

    accuracy                           0.97       248
   macro avg       0.92      0.85      0.86       248
weighted avg       0.97      0.97      0.97       248

Precision  0.9742525876796302
f1 Score  0.9678443365486884
Recall  0.967741935483871
Specificity/TNR: 1.0
Cohen Kappa: 0.859629262770624
AUC Score  0.995016379394014
Training Accuracy: 0.908
Testing Accuracy: 0.944
[[ 22   0   1]
 [  3   1   3]
 [  7   0 211]]
              precision    recall  f1-score   support

           0       0.69      0.96      0.80        23
           1       1.00      0.14      0.25         7
           2       0.98      0.97      0.97       218

    accuracy                           0.94       248
   macro avg       0.89      0.69      0.67       248
weighted avg       0.95      0.9

C:\Users\babar\anaconda3\lib\site-packages\sklearn\utils\validation.py:993: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\babar\anaconda3\lib\site-packages\sklearn\utils\validation.py:993: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\babar\anaconda3\lib\site-packages\sklearn\utils\validation.py:993: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\babar\anaconda3\lib\site-packages\sklearn\utils\validation.py:993: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), 

...

C:\Users\babar\anaconda3\lib\site-packages\sklearn\utils\validation.py:993: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\babar\anaconda3\lib\site-packages\sklearn\utils\validation.py:993: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\babar\anaconda3\lib\site-packages\sklearn\utils\validation.py:993: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\babar\anaconda3\lib\site-packages\sklearn\utils\validation.py:993: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), 


              precision    recall  f1-score   support

           0       0.69      0.87      0.77        23
           1       1.00      0.43      0.60         7
           2       0.98      0.97      0.98       218

    accuracy                           0.95       248
   macro avg       0.89      0.76      0.78       248
weighted avg       0.95      0.95      0.95       248

Precision  0.9549396448729041
f1 Score  0.9470534928131183
Recall  0.9475806451612904
Specificity/TNR: 1.0
Cohen Kappa: 0.7651515151515151
AUC Score  0.9653491761630302
Training Accuracy: 0.919
Testing Accuracy: 0.940
[[ 21   1   1]
 [  3   1   3]
 [  6   1 211]]
              precision    recall  f1-score   support

           0       0.70      0.91      0.79        23
           1       0.33      0.14      0.20         7
           2       0.98      0.97      0.97       218

    accuracy                           0.94       248
   macro avg       0.67      0.67      0.66       248
weighted avg       0.94     

C:\Users\babar\anaconda3\lib\site-packages\sklearn\utils\validation.py:993: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\babar\anaconda3\lib\site-packages\sklearn\utils\validation.py:993: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\babar\anaconda3\lib\site-packages\sklearn\utils\validation.py:993: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\babar\anaconda3\lib\site-packages\sklearn\utils\validation.py:993: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), 

              precision    recall  f1-score   support

           0       0.70      0.91      0.79        23
           1       0.33      0.14      0.20         7
           2       0.98      0.97      0.97       218

    accuracy                           0.94       248
   macro avg       0.67      0.67      0.66       248
weighted avg       0.94      0.94      0.94       248

Precision  0.9370061265316328
f1 Score  0.9358399550757008
Recall  0.9395161290322581
Specificity/TNR: 0.9545454545454546
Cohen Kappa: 0.7328162034044388
AUC Score  0.9760133137237909
0.9475806451612904
0.9475806451612904
[[ 21   0   2]
 [  1   2   4]
 [  4   2 212]]
              precision    recall  f1-score   support

           0       0.81      0.91      0.86        23
           1       0.50      0.29      0.36         7
           2       0.97      0.97      0.97       218

    accuracy                           0.95       248
   macro avg       0.76      0.72      0.73       248
weighted avg       0.94  

C:\Users\babar\anaconda3\lib\site-packages\sklearn\neighbors\_classification.py:198: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  return self._fit(X, y)


In [7]:
hyper_params["SVC"] = svc_param
hyper_params["LR"] = lr_param
hyper_params["KNN"] = knn_param

In [8]:
hyper_params

{'Column': ['Feature 4', 'Feature 5', 'Feature 7', 'Feature 9'],
 'SVC': [{'C': 14, 'gamma': 0.1, 'kernel': 'rbf'},
  {'C': 15, 'gamma': 0.1, 'kernel': 'rbf'},
  {'C': 9, 'gamma': 0.1, 'kernel': 'rbf'},
  {'C': 6, 'gamma': 0.1, 'kernel': 'rbf'}],
 'LR': [{'C': 2.7825594022071245, 'penalty': 'l1', 'solver': 'saga'},
  {'C': 2.7825594022071245, 'penalty': 'l2', 'solver': 'saga'},
  {'C': 7.742636826811269, 'penalty': 'l2', 'solver': 'saga'},
  {'C': 2.7825594022071245, 'penalty': 'l1', 'solver': 'saga'}],
 'KNN': [{'metric': 'manhattan', 'n_neighbors': 17, 'weights': 'distance'},
  {'metric': 'manhattan', 'n_neighbors': 7, 'weights': 'distance'},
  {'metric': 'manhattan', 'n_neighbors': 14, 'weights': 'distance'},
  {'metric': 'manhattan', 'n_neighbors': 13, 'weights': 'distance'}]}

In [9]:
hyper_params_df = pd.DataFrame.from_dict(hyper_params)
hyper_params_df

Column                                       SVC  \
0  Feature 4  {'C': 14, 'gamma': 0.1, 'kernel': 'rbf'}   
1  Feature 5  {'C': 15, 'gamma': 0.1, 'kernel': 'rbf'}   
2  Feature 7   {'C': 9, 'gamma': 0.1, 'kernel': 'rbf'}   
3  Feature 9   {'C': 6, 'gamma': 0.1, 'kernel': 'rbf'}   

                                                  LR  \
0  {'C': 2.7825594022071245, 'penalty': 'l1', 'so...   
1  {'C': 2.7825594022071245, 'penalty': 'l2', 'so...   
2  {'C': 7.742636826811269, 'penalty': 'l2', 'sol...   
3  {'C': 2.7825594022071245, 'penalty': 'l1', 'so...   

                                                 KNN  
0  {'metric': 'manhattan', 'n_neighbors': 17, 'we...  
1  {'metric': 'manhattan', 'n_neighbors': 7, 'wei...  
2  {'metric': 'manhattan', 'n_neighbors': 14, 'we...  
3  {'metric': 'manhattan', 'n_neighbors': 13, 'we...

In [10]:
hyper_params_df.to_csv("EI 70-30 Applying RF Hyper-parameters.csv", index=False)